# Group 27

Submission until 23 Jan 23:59 via https://forms.gle/n6ERdhYx3uBPzuGn9

In [1]:
!pip install -q -U tensorflow-text

In [2]:
!pip install nltk

In [3]:
from google.colab import drive
import re
import tensorflow_text as tf_txt
import tensorflow as tf
import nltk

# 1. Dataset

In [4]:
# mount drive to google colab
from google.colab import drive
drive.mount('/content/gdrive')

# change the working directory
%cd /content/gdrive/My Drive/IANNwTF

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).
/content/gdrive/My Drive/IANNwTF


In [5]:
 # load text file
 bible = open('bible.txt','r').read()

### Preprocessing

In [6]:
# convert string to lower case
bible = bible.lower()
# remove new-line characters
bible = bible.replace('\n', ' ')
bible = re.sub('\s{2,}', ' ', bible) # to remove more than one space 
# remove special characters (keep letters, numbers, space)
bible = re.sub(r"[^a-zA-Z0-9 ]","", bible)

In [7]:
bible

'the first book of moses called genesis 11 in the beginning god created the heaven and the earth 12 and the earth was without form and void and darkness was upon the face of the deep and the spirit of god moved upon the face of the waters 13 and god said let there be light and there was light 14 and god saw the light that it was good and god divided the light from the darkness 15 and god called the light day and the darkness he called night and the evening and the morning were the first day 16 and god said let there be a firmament in the midst of the waters and let it divide the waters from the waters 17 and god made the firmament and divided the waters which were under the firmament from the waters which were above the firmament and it was so 18 and god called the firmament heaven and the evening and the morning were the second day 19 and god said let the waters under the heaven be gathered together unto one place and let the dry land appear and it was so 110 and god called the dry la

In [25]:
# tokenize the string into word-tokens using a word-level tokenizer
splitter = tf_txt.RegexSplitter(split_regex=' ')
tokens = splitter.split(bible)

In [27]:
# find the 10.000 most common words
fdist = nltk.probability.FreqDist(word for word in nltk.tokenize.word_tokenize(bible))
mostCommon = []
for word, counter in fdist.most_common(10000):
  mostCommon.append(word)
mostCommon[:10]

['the', 'and', 'of', 'to', 'that', 'in', 'he', 'shall', 'unto', 'for']

In [10]:
# create a vocabulary to save mappings from tokens to integer indices
vocab, index = {}, 1  # start indexing from 1
vocab['<pad>'] = 0  # add a padding token
for token in tokens:
  if token not in vocab:
    vocab[token] = index
    index += 1
vocab_size = len(vocab)

In [11]:
# create an inverse vocabulary to save mappings from integer indices to tokens
inverse_vocab = {index: token for token, index in vocab.items()}
print(inverse_vocab)

{0: '<pad>', 1: 'the', 2: 'first', 3: 'book', 4: 'of', 5: 'moses', 6: 'called', 7: 'genesis', 8: '11', 9: 'in', 10: 'beginning', 11: 'god', 12: 'created', 13: 'heaven', 14: 'and', 15: 'earth', 16: '12', 17: 'was', 18: 'without', 19: 'form', 20: 'void', 21: 'darkness', 22: 'upon', 23: 'face', 24: 'deep', 25: 'spirit', 26: 'moved', 27: 'waters', 28: '13', 29: 'said', 30: 'let', 31: 'there', 32: 'be', 33: 'light', 34: '14', 35: 'saw', 36: 'that', 37: 'it', 38: 'good', 39: 'divided', 40: 'from', 41: '15', 42: 'day', 43: 'he', 44: 'night', 45: 'evening', 46: 'morning', 47: 'were', 48: '16', 49: 'a', 50: 'firmament', 51: 'midst', 52: 'divide', 53: '17', 54: 'made', 55: 'which', 56: 'under', 57: 'above', 58: 'so', 59: '18', 60: 'second', 61: '19', 62: 'gathered', 63: 'together', 64: 'unto', 65: 'one', 66: 'place', 67: 'dry', 68: 'land', 69: 'appear', 70: '110', 71: 'gathering', 72: 'seas', 73: '111', 74: 'bring', 75: 'forth', 76: 'grass', 77: 'herb', 78: 'yielding', 79: 'seed', 80: 'fruit', 8

In [12]:
# vectorize the bible
sequence = [vocab[word] for word in tokens]

In [13]:
# generate skip-grams (input-target pairs)
window_size = 2
positive_skip_grams, _ = tf.keras.preprocessing.sequence.skipgrams(
      sequence,
      vocabulary_size=vocab_size,
      window_size=window_size,
      negative_samples=0)

3284470


In [33]:
# create tf dataset from the skip grams
targets = []
inputs = []
for (target, context) in positive_skip_grams:
  targets.append(target)
  inputs.append(context)

dataset = tf.data.Dataset.from_tensor_slices((inputs, targets))

In [48]:
# subset of the vocab containing only the 10 000 most common words
vocab_mostCommon = { key: vocab[key] for key in mostCommon }

In [50]:
# filter the dataset to only keep skip grams with the most common targets
def dataset_fn(ds):
  return ds.filter(lambda input, target: target in vocab_mostCommon)

dataset = dataset.apply(dataset_fn)

TypeError: ignored

In [54]:
# other filter method
def filter_fn(x, y):
  return y in vocab_mostCommon

dataset = dataset.filter(filter_fn)

TypeError: ignored

# 2. Model

# 3. Training